## Import Libraries

In [2]:
import numpy as np
import pandas as pd
import allel
import tsinfer
import tskit

/Users/yagishinnosuke/Documents/2024-2025 Stanford/Research/Selective-Sweep-Simulation/venv-lct/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Load and Parse the VCF

In [22]:
# Load the VCF
vcf_file = "/Users/yagishinnosuke/Documents/2024-2025 Stanford/Research/Selective-Sweep-Simulation/1000genomes/LCT_region.vcf"

callset = allel.read_vcf(
    vcf_file,
    fields=["samples", "variants/POS", "variants/REF", "variants/ALT", "calldata/GT"]
)

# Extract the genotype and position info
samples = callset['samples']
positions = callset['variants/POS']
genotypes = allel.GenotypeArray(callset['calldata/GT'])

print(f"Samples: {len(samples)}")
print(f"Variants: {len(positions)}")

Samples: 2504
Variants: 57869


## Convert Genotypes to Haplotypes

In [23]:
# Convert to haplotypes (shape: n_variants x 2*n_samples)
haplotypes = genotypes.to_haplotypes()

print("Haplotypes shape:", haplotypes.shape)

Haplotypes shape: (57869, 5008)


### Filter Out Sites with Missing Data (just in case)

In [24]:
# Keep only variants with no missing data
is_called = genotypes.is_called().all(axis=1)
haplotypes = haplotypes[is_called]
positions = positions[is_called]

print(f"Filtered to {haplotypes.shape[0]} variants with complete data.")

Filtered to 57869 variants with complete data.


## Build the tsinfer.SampleData Object

In [25]:
alts = callset["variants/ALT"]
# ALT is a NumPy array of shape (num_variants, max_alt_length)
# Check whether there's only one non-empty alt allele per site
is_biallelic = np.array([(alt[0] != '') and (alt[1] == '') for alt in alts])

In [26]:
is_called = genotypes.is_called().all(axis=1)
combined_filter = is_biallelic & is_called

genotypes_filtered = genotypes[combined_filter]
positions_filtered = positions[combined_filter]
haplotypes_filtered = genotypes_filtered.to_haplotypes()

print(f"Remaining biallelic, fully-called variants: {haplotypes_filtered.shape[0]}")

Remaining biallelic, fully-called variants: 57573


In [27]:
# Combine into DataFrame to keep positions and haplotypes synced
df = pd.DataFrame({
    "pos": positions_filtered
})
df["idx"] = df.index  # Track original index

# Drop duplicate positions, keeping the first
df_unique = df.drop_duplicates(subset="pos", keep="first").sort_values("pos")

# Apply filter to positions and haplotypes
positions_final = df_unique["pos"].values
haplotypes_final = haplotypes_filtered[df_unique["idx"].values]

print(f"Final unique & sorted variants: {len(positions_final)}")

Final unique & sorted variants: 57521


In [28]:
sample_data = tsinfer.SampleData(path="/Users/yagishinnosuke/Documents/2024-2025 Stanford/Research/Selective-Sweep-Simulation/1000genomes/lct_samples.trees", sequence_length=int(positions_final[-1]) + 1)

num_individuals = haplotypes_final.shape[1] // 2
for _ in range(num_individuals):
    sample_data.add_individual(ploidy=2)

for i, pos in enumerate(positions_final):
    g = haplotypes_final[i]
    sample_data.add_site(position=int(pos), genotypes=g)

sample_data.finalise()
print("Sample data written to lct_samples.trees")

/Users/yagishinnosuke/Documents/2024-2025 Stanford/Research/Selective-Sweep-Simulation/venv-lct/lib/python3.11/site-packages/tsinfer/formats.py:524: FutureWarning: The LMDBStore is deprecated and will be removed in a Zarr-Python version 3, see https://github.com/zarr-developers/zarr-python/issues/1274 for more information.
  return zarr.LMDBStore(self.path, subdir=False, map_size=map_size)
/var/folders/db/c7lgtr1d5s338q2r1_vmvc1w0000gn/T/ipykernel_43965/1305666011.py:1: DeprecationWarning: SampleData is deprecated
  sample_data = tsinfer.SampleData(path="/Users/yagishinnosuke/Documents/2024-2025 Stanford/Research/Selective-Sweep-Simulation/1000genomes/lct_samples.trees", sequence_length=int(positions_final[-1]) + 1)


Sample data written to lct_samples.trees


/Users/yagishinnosuke/Documents/2024-2025 Stanford/Research/Selective-Sweep-Simulation/venv-lct/lib/python3.11/site-packages/tsinfer/formats.py:103: FutureWarning: The LMDBStore is deprecated and will be removed in a Zarr-Python version 3, see https://github.com/zarr-developers/zarr-python/issues/1274 for more information.
  store = zarr.LMDBStore(


In [29]:
sample_data = tsinfer.load("/Users/yagishinnosuke/Documents/2024-2025 Stanford/Research/Selective-Sweep-Simulation/1000genomes/lct_samples.trees")  # Load from file if needed
ts = tsinfer.infer(sample_data, progress_monitor=True)
ts.dump("lct_inferred.trees")
print("Inference complete — tree sequence saved to lct_inferred.trees")

ga-add   (1/6)100%|██████████| 57.5k/57.5k [00:02, 26.5kit/s]
ga-gen   (2/6)100%|██████████| 25.9k/25.9k [00:12, 2.07kit/s]



ms-muts  (4/6)100%|██████████| 32.8k/32.8k [00:00, 137kit/s]
ma-match (3/6)100%|██████████| 25.9k/25.9k [17:57, 24.0it/s]
ms-match (5/6)100%|██████████| 5.01k/5.01k [23:56, 3.49it/s]
ms-paths (6/6)100%|██████████| 5.01k/5.01k [00:00, 13.4kit/s]
ms-muts  (7/6)100%|██████████| 32.8k/32.8k [00:00, 134kit/s]
ms-xsites (8/6)100%|██████████| 24.7k/24.7k [00:12, 2.03kit/s]


Inference complete — tree sequence saved to lct_inferred.trees


In [ ]:
# Zoom in on a specific tree along the genome
tree = ts.at(positions_final[len(positions_final) // 2])  # Middle of the region
tree.draw_svg(size=(1000, 400))


In [4]:
ts = tskit.load("lct_inferred.trees")

print("Number of trees:", ts.num_trees)
print("Number of SNPs (sites):", ts.num_sites)
print("Sequence length:", ts.sequence_length)

Number of trees: 24675
Number of SNPs (sites): 57521
Sequence length: 137999972.0


## create PLINK map file (unrelated)

In [5]:
# Load the IMPUTE-style map
df = pd.read_csv("../1000genomes/genetic_map_chr2_combined_b37.txt", delim_whitespace=True)

# Convert to PLINK-style format
plink_df = pd.DataFrame({
    'chr': 2,
    'snp_id': 'rs' + df['position'].astype(str),  # dummy SNP ID
    'cM': df['Genetic_Map(cM)'],
    'bp': df['position']
})

# Save as tab-separated
plink_df.to_csv("chr2_plink.map", sep='\t', index=False, header=False)

/var/folders/db/c7lgtr1d5s338q2r1_vmvc1w0000gn/T/ipykernel_64769/4020374792.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_csv is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_csv("../1000genomes/genetic_map_chr2_combined_b37.txt", delim_whitespace=True)


## Selection Labeling Pipeline

In [11]:
ibd_columns = [
    "id1", "hap1", "id2", "hap2", "chrom", "marker1", "marker2", "length_cM"
]

ibd_df = pd.read_csv("../1000genomes/chr2_ibd.ibd.gz", delim_whitespace=True, names=ibd_columns)
print(ibd_df.head())

       id1  hap1      id2  hap2  chrom    marker1    marker2  length_cM
0  HG03971     1  HG04210     2      2   30304587   31112507      2.088
1  HG02164     2  HG02397     1      2  234829543  235423318      2.137
2  NA19703     2  NA19711     2      2  234928982  235487224      2.024
3  HG02391     2  HG02397     2      2  235014341  235627087      2.024
4  HG02353     2  HG02379     2      2  235425594  235985286      2.311


/var/folders/db/c7lgtr1d5s338q2r1_vmvc1w0000gn/T/ipykernel_64769/3352017896.py:5: FutureWarning: The 'delim_whitespace' keyword in pd.read_csv is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  ibd_df = pd.read_csv("../1000genomes/chr2_ibd.ibd.gz", delim_whitespace=True, names=ibd_columns)


In [40]:
# Define window size and region of interest
window_size = 20_000
start_pos = 135_750_000
end_pos = 138_000_000

# Define windows ONLY in the LCT region
windows = pd.DataFrame({
    'start': np.arange(start_pos, end_pos, window_size)
})
windows['end'] = windows['start'] + window_size

# Count IBD overlaps per window
def count_ibd(row):
    return np.sum(
        (ibd_df['marker1'] < row['end']) &
        (ibd_df['marker2'] > row['start'])
    )

windows['ibd_count'] = windows.apply(count_ibd, axis=1)

# Label top 1% of windows
top_n = int(len(windows) * 0.10)
windows['rank'] = windows['ibd_count'].rank(method='first', ascending=False)
windows['label'] = (windows['rank'] <= top_n).astype(int)
windows.drop(columns='rank', inplace=True)

print(windows['label'].value_counts())  # Sanity check

# Load the inferred tree sequence
ts = tskit.load("../1000genomes/lct_inferred.trees")

# Match each tree to overlapping window
tree_regions = []
tree_labels = []

for tree in ts.trees():
    start, end = map(int, tree.interval)
    
    # Check if tree overlaps any labeled window
    overlapping = windows[(windows['start'] < end) & (windows['end'] > start)]
    
    if not overlapping.empty:
        label = int((overlapping['label'] == 1).any())
        tree_regions.append((start, end))
        tree_labels.append(label)

# Report result
import collections
print("🧾 Tree label counts:", collections.Counter(tree_labels))

label
0    102
1     11
Name: count, dtype: int64
🧾 Tree label counts: Counter({0: 24673, 1: 2})


In [42]:
print(windows[windows['label'] == 1].head(10))


       start        end  ibd_count  label
0  135750000  135770000          0      1
1  135770000  135790000          0      1
2  135790000  135810000          0      1
3  135810000  135830000          0      1
4  135830000  135850000          0      1
5  135850000  135870000          0      1
6  135870000  135890000          0      1
7  135890000  135910000          0      1
8  135910000  135930000          0      1
9  135930000  135950000          0      1


In [41]:
import csv

with open("../1000genomes/tree_selection_labels.csv", "w", newline="") as f:
    writer = csv.writer(f)
    writer.writerow(["tree_index", "start", "end", "label"])
    for i, (interval, label) in enumerate(zip(tree_regions, tree_labels)):
        writer.writerow([i, interval[0], interval[1], label])